<a href="https://colab.research.google.com/github/TheorChemGroup/Glucose_Biosensor/blob/main/main.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Импорт необходимых библиотек

In [183]:
# Data vizualization
import plotly.graph_objs as go
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.io as pio

pio.templates.default = "plotly_white"

In [184]:
# Base libraries
import pandas as pd
import numpy as np
from typing import List, Tuple
import warnings
warnings.filterwarnings("ignore")

In [453]:
# ML libraries
from pycaret.classification import ClassificationExperiment
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.ensemble import RandomForestClassifier, ExtraTreesClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.svm import SVC
from sklearn.metrics import balanced_accuracy_score, accuracy_score, f1_score
from sklearn.preprocessing import StandardScaler, MinMaxScaler

# Обработка данных

In [186]:
experiments: List[pd.DataFrame] = []

In [187]:
# Read experiment time limits pages from excel
def read_limits(sheet_name: str) -> List[Tuple]:
    data = pd.read_excel("results.xlsx", sheet_name=sheet_name, header=2)
    data.drop([col for col in data.columns if "ответ" in col], axis=1, inplace=True)
    data = data.apply(lambda x: x.str.replace(',', '.'))

    limits = []

    for col in data.columns:
        pair = data[col].str.split("-", expand=True)
        pair.drop(pair.loc[(pair[0] == "") | (pair[1] == "")], inplace=True)

        limits.append(
            list(
                zip(
                    pair[0].astype(float).values,
                    pair[1].astype(float).values,
                )
            )
        )

    return limits

In [188]:
# Read experiment data
def extract_experiments(data: pd.DataFrame, limit: List[Tuple[float, float]]) -> List[pd.DataFrame]:
    # Remove NaN tail if exist
    last_valid = data[data["time"].notnull()].index[-1]
    data = data[:last_valid]

    curves = None
    lims = None

    # Find machine restart joints
    joints = list(data[data["time"].isna()].index)

    # Divide data by joints
    if len(joints) != 0:
        parts = []
        prev = 0
        for joint in joints:
            parts.append(data[prev:joint])
            prev = joint + 1

        parts.append(data[prev:])
        curves = parts
    else: curves = data

    # Divide limits by found joints
    if len(joints) != 0:
        prev = 0
        lim_joints = []
        lim_parts = []
        for i, (start, _) in enumerate(limit):
            if start < prev:
                lim_joints.append(i)
            prev = start


        prev = 0
        for joint in lim_joints:
            lim_parts.append(limit[prev:joint])
            prev = joint + 1
        lim_parts.append(limit[prev:])
        lims = lim_parts
    else: lims = limit

    experiments = []

    # Experiment list fill
    if len(joints) == 0:
        curves.set_index("time", inplace=True)
        for i, lim in enumerate(lims):
            start, end = lim
            experiments.append(curves[start:end])
    else:
        for i in range(len(curves)):
            curves[i].set_index("time", inplace=True)
            for j, lim in enumerate(lims[i]):
                start, end = lim
                experiments.append(curves[i][start:end])

    return experiments

In [189]:
# Read two experiments for single specific reagent
def parse_data(limit_sheet_name: str, sheet_names: Tuple[str, str]):
    data_10mkl_1 = pd.read_excel("results.xlsx", sheet_name=sheet_names[0], header=1)
    data_10mkl_1 = data_10mkl_1[data_10mkl_1.columns[:2]]
    data_10mkl_1.columns = ["current", "time"]
    data_10mkl_2 = pd.read_excel("results.xlsx", sheet_name=sheet_names[1], header=1)
    data_10mkl_2 = data_10mkl_2[data_10mkl_2.columns[:2]]
    data_10mkl_2.columns = ["current", "time"]

    data_20mkl_1 = pd.read_excel("results.xlsx", sheet_name=sheet_names[0], header=1)
    data_20mkl_1 = data_20mkl_1[data_20mkl_1.columns[2:4]]
    data_20mkl_1.columns = ["current", "time"]
    data_20mkl_2 = pd.read_excel("results.xlsx", sheet_name=sheet_names[1], header=1)
    data_20mkl_2 = data_20mkl_2[data_20mkl_2.columns[2:4]]
    data_20mkl_2.columns = ["current", "time"]

    data_30mkl_1 = pd.read_excel("results.xlsx", sheet_name=sheet_names[0], header=1)
    data_30mkl_1 = data_30mkl_1[data_30mkl_1.columns[-2:]]
    data_30mkl_1.columns = ["current", "time"]
    data_30mkl_2 = pd.read_excel("results.xlsx", sheet_name=sheet_names[1], header=1)
    data_30mkl_2 = data_30mkl_2[data_30mkl_2.columns[-2:]]
    data_30mkl_2.columns = ["current", "time"]

    limits = read_limits(limit_sheet_name)

    exp_10mkl = []
    exp_20mkl = []
    exp_30mkl = []

    exp_10mkl.append(extract_experiments(data=data_10mkl_1, limit=limits[0]))
    exp_10mkl.append(extract_experiments(data=data_10mkl_2, limit=limits[3]))

    if limit_sheet_name != "гл+глутатитон":
        exp_20mkl.append(extract_experiments(data=data_20mkl_1, limit=limits[1]))
    exp_20mkl.append(extract_experiments(data=data_20mkl_2, limit=limits[4]))

    exp_30mkl.append(extract_experiments(data=data_30mkl_1, limit=limits[2]))
    exp_30mkl.append(extract_experiments(data=data_30mkl_2, limit=limits[5]))

    return exp_10mkl, exp_20mkl, exp_30mkl

In [237]:
glu = parse_data(limit_sheet_name="глюкоза", sheet_names=("гл-графики (1)", "гл-графики (2)"))
glu_glut = parse_data(limit_sheet_name="гл+глутатитон", sheet_names=("гл+глут графики (1)", "гл+глут графики (2)"))
glu_ask = parse_data(limit_sheet_name="гл+аск. к-та", sheet_names=("гл+аск. к-та графики (1)", "гл+аск. к-та графики (2)"))
glu_cist = parse_data(limit_sheet_name="гл+цистеин", sheet_names=("гл+цистеин графики (1)", "гл+цистеин графики (2)"))

data = {
    "glu": {
        10: glu[0],
        20: glu[1],
        30: glu[2],
    },
    "glu+glut": {
        10: glu_glut[0],
        20: glu_glut[1],
        30: glu_glut[2],
    },
    "glu+ask": {
        10: glu_ask[0],
        20: glu_ask[1],
        30: glu_ask[2],
    },
    "glu+cist": {
        10: glu_cist[0],
        20: glu_cist[1],
        30: glu_cist[2],
    },
}

In [191]:
fig = go.Figure()

types = {
    "glu": "solid",
    "glu+glut": "dot",
    "glu+ask": "dot",
    "glu+cist": "dot",
}

colors = px.colors.qualitative.Plotly
colors.extend([
    "green",
    "darkorange",
    "pink",
    "crimson",
    "teal",
    "brown",
    "coral",
    "firebrick",
    "gold",
    "orangered",
    "olivedrab",
    "orchid",
    "salmon",
    "slateblue",
])

k = 0
b = 0
for key in data.keys():
    k = b
    for i, exp in enumerate(data[key][10], start=k):
        for val in exp:
            fig.add_trace(
                go.Scatter(x=val.index, y=val["current"], opacity=.6, legendgroup=types[key], showlegend=False, line=dict(dash=types[key], color=colors[i]), name=f"№{i+1}")
            )
    k = i
    for i, exp in enumerate(data[key][20], start=k):
        for val in exp:
            fig.add_trace(
                go.Scatter(x=val.index, y=val["current"], opacity=.6, legendgroup=types[key], showlegend=False, line=dict(dash=types[key], color=colors[i]), name=f"№{i+1}")
            )
    k = i
    for i, exp in enumerate(data[key][30], start=k):
        for val in exp:
            fig.add_trace(
                go.Scatter(x=val.index, y=val["current"], opacity=.6, legendgroup=types[key], showlegend=False, line=dict(dash=types[key], color=colors[i]), name=f"№{i+1}")
            )
    b = i

fig.add_trace(
    go.Scatter(x=[None], y=[None], showlegend=True, legendgroup="solid", name="Без примесей")
)
fig.add_trace(
    go.Scatter(x=[None], y=[None], showlegend=True, legendgroup="dot", name="С примесями", line=dict(dash="dot"))
)

fig.update_layout(title_text="Зависимость силы тока от времени", title_x=.5, height=700)
fig.update_xaxes(title_text="Время, с")
fig.update_yaxes(title_text="Сила тока, А")

fig.show()
fig.write_html("out.html")

In [458]:
with open("experiments_mypars.pickle", 'rb') as f:
    exps = pickle.load(f)

120

In [239]:
data = {
    "glu": {
        10: [item for part in data["glu"][10] for item in part],
        20: [item for part in data["glu"][20] for item in part],
        30: [item for part in data["glu"][30] for item in part],
    },
    "glu+glut": {
        10: [item for part in data["glu+glut"][10] for item in part],
        20: [item for part in data["glu+glut"][20] for item in part],
        30: [item for part in data["glu+glut"][30] for item in part],
    },
    "glu+ask": {
        10: [item for part in data["glu+ask"][10] for item in part],
        20: [item for part in data["glu+ask"][20] for item in part],
        30: [item for part in data["glu+ask"][30] for item in part],
    },
    "glu+cist": {
        10: [item for part in data["glu+cist"][10] for item in part],
        20: [item for part in data["glu+cist"][20] for item in part],
        30: [item for part in data["glu+cist"][30] for item in part],
    },
}

In [465]:
glu = [
    *data["glu"][10], *data["glu"][20], *data["glu"][30],
]
glu_glut = [
    *data["glu+glut"][10], *data["glu+glut"][20], *data["glu+glut"][30],
]
glu_ask = [
    *data["glu+ask"][10], *data["glu+ask"][20], *data["glu+ask"][30],
]
glu_cist = [
    *data["glu+cist"][10], *data["glu+cist"][20], *data["glu+cist"][30],
]

x = list(map(lambda x: np.array(x), [
    *exps[0],
    *exps[1],
    *exps[2],
    *exps[3],
]))

labels = np.concatenate([
    np.zeros(len(exps[0])),
    np.ones(len(exps[1])),
    np.ones(len(exps[2])),
    np.ones(len(exps[3])),
])

In [466]:
def extract_features(x):
    if x.shape[0] == 0: return
    p20 = np.poly1d(np.polyfit(range(x.shape[0]), x.reshape(-1), 20))
    result = np.array(p20(np.linspace(0, x.shape[0], 30)))
    return result

In [467]:
X = []
y = []
max_ = 0
durations = []
for i in range(len(x)):
    v = extract_features(x[i])
    if v is not None:
        v += abs(v[0])
        max_ = max(max_, v.max())
        durations.append(x[i].shape[0] / 10)

        X.append(v)
        y.append(labels[i])

X /= max_
tmp = []
for i in range(len(X)):
    tmp.append(np.append(X[i], [X[i].min(), X[i].max(), durations[i]]))

In [468]:
X = np.stack(tmp)
y = np.array(y)

In [469]:
df = pd.DataFrame(X)
df["target"] = y
df.columns = list(map(str, df.columns))

In [470]:
df.shape

(462, 34)

In [471]:
fig = go.Figure()
for e in X:
    fig.add_trace(
        go.Scatter(x=list(range(34)), y=e)
    )

fig.show()

In [472]:
scaler = MinMaxScaler()
data_norm = scaler.fit_transform(df)
df_norm = pd.DataFrame(data_norm, columns=df.columns)

# Обучение моделей машинного обучения

In [473]:
s = ClassificationExperiment()
s.setup(df, target="target", session_id=12345)
s.add_metric("balanced_accuracy", "Balanced Accuracy", balanced_accuracy_score, greater_is_better=True)

best = s.compare_models(cross_validation=False)

Processing:   0%|          | 0/65 [00:00<?, ?it/s]

In [431]:
rf = s.create_model("rf", cross_validation=False)
lgbm = s.create_model("lightgbm", cross_validation=False)
gbc = s.create_model("gbc", cross_validation=False)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [474]:
tuned_lgbm = s.tune_model(lgbm, optimize="Balanced Accuracy", n_iter=30)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 10 folds for each of 30 candidates, totalling 300 fits


In [433]:
tuned_rf = s.tune_model(rf, optimize="Balanced Accuracy", n_iter=50)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 10 folds for each of 50 candidates, totalling 500 fits


In [434]:
tuned_gbc = s.tune_model(gbc, optimize="Balanced Accuracy", n_iter=50)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 10 folds for each of 50 candidates, totalling 500 fits


In [438]:
svm = s.create_model("svm", cross_validation=False)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [450]:
X_train, X_test, y_train, y_test = train_test_split(df_norm.drop(["target"], axis=1), df_norm["target"], test_size=.25, shuffle=True, random_state=12345)

In [451]:
models = [
    # {
    #     "estimator": KNeighborsClassifier(),
    #     "param_grid": {
    #         "n_neighbors": np.arange(3, 20, 2),
    #         "leaf_size": np.arange(10, 80, 5),
    #     },
    # },
    {
        "estimator": RandomForestClassifier(random_state=12345),
        "param_grid": {
            "n_estimators": np.arange(10, 500, 5),
        },
    },
    # {
    #     "estimator": ExtraTreesClassifier(random_state=12345),
    #     "param_grid": {
    #         "n_estimators": np.arange(10, 300, 10),
    #     },
    # },
]

In [452]:
for model in models:
    cv = GridSearchCV(
        estimator=model["estimator"],
        param_grid=model["param_grid"],
        n_jobs=-1,
        cv=10,
        scoring="balanced_accuracy",
    )
    cv.fit(X_train, y_train)
    print(f"Estimator: {cv.estimator}")
    print(f"Best score: {cv.best_score_}")
    print(f"Best parameters: {cv.best_params_}")
    print()

Estimator: RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight=None,
                       criterion='gini', max_depth=None, max_features='sqrt',
                       max_leaf_nodes=None, max_samples=None,
                       min_impurity_decrease=0.0, min_samples_leaf=1,
                       min_samples_split=2, min_weight_fraction_leaf=0.0,
                       n_estimators=100, n_jobs=None, oob_score=False,
                       random_state=12345, verbose=0, warm_start=False)
Best score: 0.7643127705627705
Best parameters: {'n_estimators': 55}



In [445]:
rf = RandomForestClassifier(n_estimators=500, random_state=12345)
rf.fit(X_train, y_train)
predictions = rf.predict(X_test)

In [446]:
fig = go.Figure()

fig.add_trace(
    go.Scatter(x=list(range(len(predictions))), y=y_test.reset_index(drop=True), mode="lines", name="target")
)
fig.add_trace(
    go.Scatter(x=list(range(len(predictions))), y=predictions, mode="lines", name="predictions", line=dict(dash="dash"))
)

fig.update_layout(
    title_text="Визуализация target и predictions",
    title_x=.5,
    xaxis=dict(
        title_text="Вхождения",
    ),
    yaxis=dict(
        title_text="Классы",
        tickvals=[0, 1],
        ticktext=["Без примесей", "С примесями"],
    )
)

fig.show()

In [447]:
acc = accuracy_score(y_test, predictions)
bal_acc = balanced_accuracy_score(y_test, predictions)
f1 = f1_score(y_test, predictions)
print(f"""Accuracy = {acc}
Balanced Accuracy = {bal_acc}
F1 Score = {f1}
""")

Accuracy = 0.8247422680412371
Balanced Accuracy = 0.7365618661257607
F1 Score = 0.8843537414965986



In [454]:
svm = SVC(kernel="linear")
svm.fit(X_train, y_train)
predictions = svm.predict(X_test)

In [455]:
acc = accuracy_score(y_test, predictions)
bal_acc = balanced_accuracy_score(y_test, predictions)
f1 = f1_score(y_test, predictions)
print(f"""Accuracy = {acc}
Balanced Accuracy = {bal_acc}
F1 Score = {f1}
""")

Accuracy = 0.6597938144329897
Balanced Accuracy = 0.4804766734279919
F1 Score = 0.7924528301886793



In [428]:
import pickle

with open('experiments.pickle', 'wb') as f:
    pickle.dump([glu, glu_glut, glu_ask, glu_cist], f)